# Cross-chapter Box 7.1 Table 1: save data in database

Saving the data in a more useful form for producing cross-chapter Box 7.1 Table 1

## Authors

All notebooks and plots in this repository were generated by the following authors:

- Zebedee Nicholls zebedee.nicholls@climate-energy-college.org
- Jared Lewis jared.lewis@climate-resource.com
- Malte Meinshausen malte.meinshausen@unimelb.edu.au

In [1]:
%load_ext nb_black

<IPython.core.display.Javascript object>

In [2]:
import os.path

import pandas as pd
import pyrcmip.assessed_ranges
import pyrcmip.database
import scmdata
import scmdata.database
import tqdm.autonotebook as tqdman

import utils

/data/ubuntu-znicholls/miniconda3/envs/ar6-wg1-plots-and-processing/lib/python3.7/site-packages/pyrcmip/assessed_ranges.py:12: TqdmExperimentalWarning: Using `tqdm.autonotebook.tqdm` in notebook mode. Use `tqdm.tqdm` instead to force console mode (e.g. in jupyter console)
  import tqdm.autonotebook as tqdman


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [3]:
assessed_ranges = pd.read_csv(utils.ASSESSED_RANGES_FILE)
assessed_ranges.head(15)

RCMIP name  \
0                     Equilibrium Climate Sensitivity   
1                          Transient Climate Response   
2             Transient Climate Response to Emissions   
3   Surface Air Ocean Blended Temperature Change W...   
4   Surface Air Temperature Change World ssp245 19...   
5                 Heat Content|Ocean ssp245 1971-2018   
6   Effective Radiative Forcing|Anthropogenic|Aero...   
7   Effective Radiative Forcing|Anthropogenic|Gree...   
8   Effective Radiative Forcing|Anthropogenic|CH4 ...   
9   Effective Radiative Forcing|Anthropogenic|CO2 ...   
10      Airborne Fraction|CO2 World 1pctCO2 1850-1920   
11      Airborne Fraction|CO2 World 1pctCO2 1850-1990   
12  Surface Air Temperature Change World ssp119 20...   
13  Surface Air Temperature Change World ssp119 20...   
14  Surface Air Temperature Change World ssp119 20...   

                                       RCMIP variable RCMIP region  \
0                                                 NaN          NaN   
1                      Surface Air Temperature Change        World   
2   Surface Air Temperature Change, Cumulative Emi...        World   
3        Surface Air Ocean Blended Temperature Change        World   
4                      Surface Air Temperature Change        World   
5                                  Heat Content|Ocean        World   
6   Effective Radiative Forcing|Anthropogenic|Aero...        World   
7   Effective Radiative Forcing|Anthropogenic|Gree...        World   
8       Effective Radiative Forcing|Anthropogenic|CH4        World   
9       Effective Radiative Forcing|Anthropogenic|CO2        World   
10  Net Ocean to Atmosphere Flux|CO2,Net Land to A...        World   
11  Net Ocean to Atmosphere Flux|CO2,Net Land to A...        World   
12                     Surface Air Temperature Change        World   
13                     Surface Air Temperature Change        World   
14                     Surface Air Temperature Change        World   

       RCMIP scenario  evaluation_period_start  evaluation_period_end  \
0                 NaN                      NaN                    NaN   
1             1pctCO2                      NaN                    NaN   
2             1pctCO2                      NaN                    NaN   
3              ssp245                   1995.0                 2014.0   
4              ssp245                   1995.0                 2014.0   
5              ssp245                   2018.0                 2018.0   
6   ssp245-1750-start                   2005.0                 2014.0   
7   ssp245-1750-start                   2019.0                 2019.0   
8   ssp245-1750-start                   2019.0                 2019.0   
9   ssp245-1750-start                   2019.0                 2019.0   
10            1pctCO2                   1920.0                 1920.0   
11            1pctCO2                   1990.0                 1990.0   
12             ssp119                   2021.0                 2040.0   
13             ssp119                   2041.0                 2060.0   
14             ssp119                   2081.0                 2100.0   

    norm_period_start  norm_period_end  very_likely__lower  likely__lower  \
0                 NaN              NaN                2.00          2.500   
1                 NaN              NaN                1.20          1.400   
2                 NaN              NaN                 NaN          1.000   
3              1850.0           1900.0                0.69            NaN   
4              1850.0           1900.0                0.67            NaN   
5              1971.0           1971.0                 NaN        329.000   
6              1750.0           1750.0               -2.00            NaN   
7              1750.0           1750.0                3.03            NaN   
8              1750.0           1750.0                0.43            NaN   
9              1750.0           1750.0                1.90            

<IPython.core.display.Javascript object>

In [4]:
assessed_ranges = pyrcmip.assessed_ranges.AssessedRanges(assessed_ranges)
sorted(assessed_ranges.db["RCMIP name"].unique())

['Airborne Fraction|CO2 World 1pctCO2 1850-1920',
 'Airborne Fraction|CO2 World 1pctCO2 1850-1990',
 'Effective Radiative Forcing|Anthropogenic|Aerosols ssp245 2005-2014',
 'Effective Radiative Forcing|Anthropogenic|CH4 ssp245 2019',
 'Effective Radiative Forcing|Anthropogenic|CO2 ssp245 2019',
 'Effective Radiative Forcing|Anthropogenic|Greenhouse Gases ssp245 2019',
 'Equilibrium Climate Sensitivity',
 'Heat Content|Ocean ssp245 1971-2018',
 'Surface Air Ocean Blended Temperature Change World ssp245 1995-2014',
 'Surface Air Temperature Change World ssp119 2021-2040',
 'Surface Air Temperature Change World ssp119 2041-2060',
 'Surface Air Temperature Change World ssp119 2081-2100',
 'Surface Air Temperature Change World ssp126 2021-2040',
 'Surface Air Temperature Change World ssp126 2041-2060',
 'Surface Air Temperature Change World ssp126 2081-2100',
 'Surface Air Temperature Change World ssp245 1995-2014',
 'Surface Air Temperature Change World ssp245 2021-2040',
 'Surface Air Tem

<IPython.core.display.Javascript object>

##  Generate output database of relevance

In [5]:
OUTPUT_DATABASE_DIR = os.path.join(
    utils.DATA_DIR, "processed", "assessed-ranges-database"
)
db = pyrcmip.database.Database(OUTPUT_DATABASE_DIR)
db

<utils.scmdata.Database (root_dir: /data2/ubuntu-znicholls/ar6-wg1-plots-and-processing/src/utils/../../data/processed/assessed-ranges-database)>

<IPython.core.display.Javascript object>

In [6]:
def save_in_database(in_db, assessed_ranges, in_db_idealised=None, extras=None):
    load_keys = []
    for metric in assessed_ranges.db["RCMIP name"]:
        try:
            to_load = assessed_ranges.get_variables_regions_scenarios_for_metric(metric)

        except TypeError:
            print(f"Not loading data for {metric}")
            continue

        assert to_load["region"] == ["World"]

        load_keys += [[v, s] for v in to_load["variable"] for s in to_load["scenario"]]

    load_keys_unique = [] if extras is None else extras
    for lk in load_keys:
        if lk in load_keys_unique:
            continue

        load_keys_unique.append(lk)

    for variable, scenario in tqdman.tqdm(load_keys_unique):
        if in_db_idealised is not None:
            if scenario == "1pctCO2":
                load_db = in_db_idealised
            else:
                load_db = in_db
        else:
            load_db = in_db

        try:
            loaded = load_db.load(
                variable=variable,
                scenario=scenario,
            )
        except ValueError:
            print(f"Could not load {variable} {scenario}")
            continue

        db.save_to_database(loaded)

<IPython.core.display.Javascript object>

## FaIR data

In [7]:
FAIR_DIR = os.path.join(
    utils.DATA_DIR,
    "raw",
    "fair",
    utils.FAIR_VERSION,
)
display(FAIR_DIR)
fair_db = scmdata.database.ScmDatabase(
    os.path.join(FAIR_DIR, "scmdatabase"),
    levels=("climate_model", "variable", "scenario"),
)

'/data2/ubuntu-znicholls/ar6-wg1-plots-and-processing/src/utils/../../data/raw/fair/v20210211'

<IPython.core.display.Javascript object>

In [8]:
fair_model_reported = os.path.join(FAIR_DIR, "impulse_response.csv")
display(fair_model_reported)
fair_model_reported = pd.read_csv(fair_model_reported).set_index("id")
fair_model_reported

'/data2/ubuntu-znicholls/ar6-wg1-plots-and-processing/src/utils/../../data/raw/fair/v20210211/impulse_response.csv'

C (W yr / m^2 / K)  C_d (W yr / m^2 / K)  \
id                                                          
median                     8.323784            122.471519   
5th percentile             6.030788             58.511844   
95th percentile           10.118715            258.464899   
156                        8.810878            448.213437   
358                        9.691545            103.494497   
...                             ...                   ...   
996792                     8.745431             62.417455   
996846                     9.089493            452.306881   
998289                     7.878012            109.737561   
998908                     9.221984            128.496448   
999021                     9.764826             47.657547   

                 alpha (W / m^2 / K)  gamma (W / m^2 / K)  \
id                                                          
median                      1.367374             0.655173   
5th percentile              0.803818             0.465854   
95th percentile             1.947091             0.893993   
156                         1.714643             0.440273   
358                         1.817834             0.772469   
...                              ...                  ...   
996792                      1.281183             0.755601   
996846                      1.881943             0.565309   
998289                      1.436389             0.522615   
998908                      1.409111             0.521846   
999021                      1.471653             0.499383   

                 kappa (W / m^2 / K)   d1 (yr)      d2 (yr)  \
id                                                            
median                      0.843767  3.696960   314.073147   
5th percentile              0.327511  2.214454   147.403762   
95th percentile             1.598579  5.649316   758.454277   
156                         0.152891  4.716124  1109.234044   
358                         1.224668  3.154765   226.416477   
...                              ...       ...          ...   
996792                      1.260458  3.369789   167.332810   
996846                      0.301282  4.160331   928.864999   
998289                      0.705869  3.656087   314.993589   
998908                      0.825368  4.101466   392.906106   
999021                      0.396387  5.164611   122.608100   

                 q1 (K / (W / m^2))  q2 (K / (W / m^2))  \
id                                                        
median                     0.443775            0.283259   
5th percentile             0.322272            0.099317   
95th percentile            0.611524            0.737910   
156                        0.535057            0.048155   
358                        0.322344            0.227762   
...                             ...                 ...   
996792                     0.377198            0.403331   
996846                     0.457376            0.073989   
998289                     0.461362            0.234828   
998908                     0.441954            0.267713   
999021                     0.522276            0.157232   

                 efficacy (dimensionless)   ecs (K)   tcr (K)  \
id                                                              
median                           1.293304  2.953389  1.814646   
5th percentile                   0.613726  2.054515  1.311732   
95th percentile                  2.000437  5.071012  2.569876   
156                              0.347264  2.115349  1.942170   
358                              1.585394  2.133679  1.274830   
...                                   ...       ...       ...   
996792                           1.668154  3.203013  1.614565   
996846                           0.532951  2.170608  1.871068   
998289                           1.350649  2.571759  1.724371   
998908                           1.581632  2.758806  1.739763   
999021                           0.793753  2.382116  1.876645

<IPython.core.display.Javascript object>

In [9]:
fair_model_reported_to_save = []

unit = "K"
cm = fair_db.available_data()["climate_model"].unique()
assert len(cm) == 1
cm = cm[0]
for ensemble_member, row in tqdman.tqdm(fair_model_reported.iterrows()):
    if any([v in ensemble_member for v in ["median", "percentile"]]):
        continue

    fair_model_reported_to_save.append(
        {
            "RCMIP name": "Equilibrium Climate Sensitivity",
            "climate_model": cm,
            "unit": unit,
            "ensemble_member": int(ensemble_member),
            "value": row[f"ecs ({unit})"],
        }
    )

fair_model_reported_to_save = pd.DataFrame(fair_model_reported_to_save)
fair_model_reported_to_save

0it [00:00, ?it/s]

RCMIP name climate_model unit  ensemble_member  \
0     Equilibrium Climate Sensitivity    FaIRv1.6.2    K              156   
1     Equilibrium Climate Sensitivity    FaIRv1.6.2    K              358   
2     Equilibrium Climate Sensitivity    FaIRv1.6.2    K              441   
3     Equilibrium Climate Sensitivity    FaIRv1.6.2    K              636   
4     Equilibrium Climate Sensitivity    FaIRv1.6.2    K              914   
...                               ...           ...  ...              ...   
2232  Equilibrium Climate Sensitivity    FaIRv1.6.2    K           996792   
2233  Equilibrium Climate Sensitivity    FaIRv1.6.2    K           996846   
2234  Equilibrium Climate Sensitivity    FaIRv1.6.2    K           998289   
2235  Equilibrium Climate Sensitivity    FaIRv1.6.2    K           998908   
2236  Equilibrium Climate Sensitivity    FaIRv1.6.2    K           999021   

         value  
0     2.115349  
1     2.133679  
2     1.800911  
3     5.331884  
4     2.902836  
...        ...  
2232  3.203013  
2233  2.170608  
2234  2.571759  
2235  2.758806  
2236  2.382116  

[2237 rows x 5 columns]

<IPython.core.display.Javascript object>

In [10]:
db.save_model_reported(fair_model_reported_to_save)

<IPython.core.display.Javascript object>

In [11]:
save_in_database(
    in_db=fair_db,
    assessed_ranges=assessed_ranges,
    extras=[["Airborne Fraction|CO2", "1pctCO2"]],
)

Not loading data for Equilibrium Climate Sensitivity


  0%|          | 0/17 [00:00<?, ?it/s]

Loading files:   0%|          | 0/1 [00:00<?, ?it/s]

Saving to database: 0it [00:00, ?it/s]

Loading files:   0%|          | 0/1 [00:00<?, ?it/s]

...

Loading files:   0%|          | 0/1 [00:00<?, ?it/s]

Saving to database: 0it [00:00, ?it/s]

Loading files:   0%|          | 0/1 [00:00<?, ?it/s]

Saving to database: 0it [00:00, ?it/s]

<IPython.core.display.Javascript object>

###  OSCAR data

In [12]:
OSCAR_DIR = os.path.join(
    utils.DATA_DIR,
    "raw",
    "oscar",
    utils.OSCAR_VERSION,
)

oscar_model_reported = os.path.join(OSCAR_DIR, "IPCC_AR6_OSCAR_indicators.csv")
oscar_model_reported = pd.read_csv(oscar_model_reported)
oscar_model_reported

RCMIP name climate_model  \
0                   Equilibrium Climate Sensitivity   OSCARv3.1.1   
1                   Equilibrium Climate Sensitivity   OSCARv3.1.1   
2                   Equilibrium Climate Sensitivity   OSCARv3.1.1   
3                   Equilibrium Climate Sensitivity   OSCARv3.1.1   
4                   Equilibrium Climate Sensitivity   OSCARv3.1.1   
...                                             ...           ...   
3227  Airborne Fraction|CO2 World 1pctCO2 1850-1990   OSCARv3.1.1   
3228  Airborne Fraction|CO2 World 1pctCO2 1850-1990   OSCARv3.1.1   
3229  Airborne Fraction|CO2 World 1pctCO2 1850-1990   OSCARv3.1.1   
3230  Airborne Fraction|CO2 World 1pctCO2 1850-1990   OSCARv3.1.1   
3231  Airborne Fraction|CO2 World 1pctCO2 1850-1990   OSCARv3.1.1   

               unit  ensemble_member     value  
0                 K                0  0.365522  
1                 K                1  1.679197  
2                 K                2  1.681227  
3                 K                3  1.837418  
4                 K                4  1.838554  
...             ...              ...       ...  
3227  dimensionless               96  0.703046  
3228  dimensionless               97  0.703127  
3229  dimensionless               98  0.703208  
3230  dimensionless               99  0.711060  
3231  dimensionless              100  0.737752  

[3232 rows x 5 columns]

<IPython.core.display.Javascript object>

In [13]:
def rename_oscar_names(v):
    replacements = (
        (
            "Effective Radiative Forcing|Aerosols ssp245 2005-2014",
            "Effective Radiative Forcing|Anthropogenic|Aerosols ssp245 2005-2014",
        ),
    )
    for old, new in replacements:
        if v == old:
            return new

    return v


oscar_model_reported["RCMIP name"] = oscar_model_reported["RCMIP name"].apply(
    rename_oscar_names
)
oscar_model_reported["RCMIP name"].unique()

array(['Equilibrium Climate Sensitivity', 'ECS_FROM_ABRUPT4XCO2_EXPT',
       'Effective Radiative Forcing|Anthropogenic|Aerosols ssp245 2005-2014',
       'Transient Climate Response to Emissions',
       'Surface Air Temperature Change World ssp245 1995-2014',
       'Surface Air Ocean Blended Temperature Change World ssp245 1995-2014',
       'Surface Air Temperature Change World ssp119 2021-2040',
       'Surface Air Temperature Change World ssp119 2041-2060',
       'Surface Air Temperature Change World ssp119 2081-2100',
       'Surface Air Temperature Change World ssp126 2021-2040',
       'Surface Air Temperature Change World ssp126 2041-2060',
       'Surface Air Temperature Change World ssp126 2081-2100',
       'Surface Air Temperature Change World ssp245 2021-2040',
       'Surface Air Temperature Change World ssp245 2041-2060',
       'Surface Air Temperature Change World ssp245 2081-2100',
       'Surface Air Temperature Change World ssp370 2021-2040',
       'Surface Air

<IPython.core.display.Javascript object>

In [14]:
db.save_model_reported(oscar_model_reported)

<IPython.core.display.Javascript object>

In [15]:
oscar_db = scmdata.database.ScmDatabase(
    os.path.join(
        OSCAR_DIR,
        "scmdatabase",
    ),
    levels=("climate_model", "variable", "scenario"),
)

<IPython.core.display.Javascript object>

In [16]:
save_in_database(in_db=oscar_db, assessed_ranges=assessed_ranges)

Not loading data for Equilibrium Climate Sensitivity


  0%|          | 0/16 [00:00<?, ?it/s]

Loading files:   0%|          | 0/1 [00:00<?, ?it/s]

Saving to database: 0it [00:00, ?it/s]

Loading files: 0it [00:00, ?it/s]

...

Loading files:   0%|          | 0/1 [00:00<?, ?it/s]

Saving to database: 0it [00:00, ?it/s]

Loading files:   0%|          | 0/1 [00:00<?, ?it/s]

Saving to database: 0it [00:00, ?it/s]

<IPython.core.display.Javascript object>

### Cicero data

In [17]:
CICERO_DIR = os.path.join(
    utils.DATA_DIR,
    "raw",
    "cicero",
    utils.CICERO_VERSION,
)
cicero_model_reported = os.path.join(
    CICERO_DIR, "rcmip-Cicero-SCM-{}-model_reported.csv".format(utils.CICERO_VERSION)
)
display(cicero_model_reported)
cicero_model_reported = pd.read_csv(cicero_model_reported)
cicero_model_reported

'/data2/ubuntu-znicholls/ar6-wg1-plots-and-processing/src/utils/../../data/raw/cicero/2.0.1/rcmip-Cicero-SCM-2.0.1-model_reported.csv'

unit     value  ensemble_member climate_model  \
0      K  2.837553               80    Cicero-SCM   
1      K  2.888126              150    Cicero-SCM   
2      K  2.700370             2420    Cicero-SCM   
3      K  2.661361             2520    Cicero-SCM   
4      K  2.758363             3110    Cicero-SCM   
..   ...       ...              ...           ...   
596    K  2.718497           303310    Cicero-SCM   
597    K  3.007575           303340    Cicero-SCM   
598    K  2.544091           303430    Cicero-SCM   
599    K  2.559833           303540    Cicero-SCM   
600    K  3.631907           303870    Cicero-SCM   

                          RCMIP name  
0    Equilibrium Climate Sensitivity  
1    Equilibrium Climate Sensitivity  
2    Equilibrium Climate Sensitivity  
3    Equilibrium Climate Sensitivity  
4    Equilibrium Climate Sensitivity  
..                               ...  
596  Equilibrium Climate Sensitivity  
597  Equilibrium Climate Sensitivity  
598  Equilibrium Climate Sensitivity  
599  Equilibrium Climate Sensitivity  
600  Equilibrium Climate Sensitivity  

[601 rows x 5 columns]

<IPython.core.display.Javascript object>

In [18]:
db.save_model_reported(cicero_model_reported)

<IPython.core.display.Javascript object>

In [19]:
cicero_db = scmdata.database.ScmDatabase(
    os.path.join(
        CICERO_DIR,
        "scmdatabase",
        #         utils.DATA_DIR,
        #         "raw",
        #         "cicero",
        #         utils.CICERO_VERSION,
    ),
    levels=("climate_model", "variable", "scenario"),
)

<IPython.core.display.Javascript object>

In [20]:
save_in_database(in_db=cicero_db, assessed_ranges=assessed_ranges)

Not loading data for Equilibrium Climate Sensitivity


  0%|          | 0/16 [00:00<?, ?it/s]

Loading files:   0%|          | 0/1 [00:00<?, ?it/s]

Saving to database: 0it [00:00, ?it/s]

Loading files: 0it [00:00, ?it/s]

...

Loading files:   0%|          | 0/1 [00:00<?, ?it/s]

Saving to database: 0it [00:00, ?it/s]

Loading files:   0%|          | 0/1 [00:00<?, ?it/s]

Saving to database: 0it [00:00, ?it/s]

<IPython.core.display.Javascript object>

###  MAGICC data

In [21]:
utils.MAGICC_OUTPUT_DIR

'/data2/ubuntu-znicholls/ar6-wg1-plots-and-processing/src/utils/../../data/raw/magicc/v20210217'

<IPython.core.display.Javascript object>

In [22]:
magicc_model_reported = os.path.join(
    utils.MAGICC_OUTPUT_DIR,
    "rcmip-magicc-model-reported.csv",
)
display(magicc_model_reported)
magicc_model_reported = pd.read_csv(magicc_model_reported)
magicc_model_reported

'/data2/ubuntu-znicholls/ar6-wg1-plots-and-processing/src/utils/../../data/raw/magicc/v20210217/rcmip-magicc-model-reported.csv'

RCMIP name     value unit  ensemble_member  \
0    Equilibrium Climate Sensitivity  3.465865    K                0   
1    Equilibrium Climate Sensitivity  7.493596    K                1   
2    Equilibrium Climate Sensitivity  3.959654    K                2   
3    Equilibrium Climate Sensitivity  2.799460    K                3   
4    Equilibrium Climate Sensitivity  3.631638    K                4   
..                               ...       ...  ...              ...   
595  Equilibrium Climate Sensitivity  2.721067    K              595   
596  Equilibrium Climate Sensitivity  5.004814    K              596   
597  Equilibrium Climate Sensitivity  4.010374    K              597   
598  Equilibrium Climate Sensitivity  2.880446    K              598   
599  Equilibrium Climate Sensitivity  3.324472    K              599   

    climate_model  
0    MAGICCv7.5.1  
1    MAGICCv7.5.1  
2    MAGICCv7.5.1  
3    MAGICCv7.5.1  
4    MAGICCv7.5.1  
..            ...  
595  MAGICCv7.5.1  
596  MAGICCv7.5.1  
597  MAGICCv7.5.1  
598  MAGICCv7.5.1  
599  MAGICCv7.5.1  

[600 rows x 5 columns]

<IPython.core.display.Javascript object>

In [23]:
db.save_model_reported(magicc_model_reported)

<IPython.core.display.Javascript object>

In [24]:
magicc_db_ssps = scmdata.database.ScmDatabase(
    os.path.join(utils.MAGICC_OUTPUT_DIR, utils.MAGICC_SSP_RCP_OUTPUT_DIR),
    levels=("climate_model", "variable", "scenario"),
)

<IPython.core.display.Javascript object>

In [25]:
magicc_db_idealised = scmdata.database.ScmDatabase(
    os.path.join(utils.MAGICC_OUTPUT_DIR, utils.MAGICC_IDEALISED_OUTPUT_DIR),
    levels=("climate_model", "variable", "scenario"),
)

<IPython.core.display.Javascript object>

In [26]:
save_in_database(
    in_db=magicc_db_ssps,
    in_db_idealised=magicc_db_idealised,
    assessed_ranges=assessed_ranges,
)

Not loading data for Equilibrium Climate Sensitivity


  0%|          | 0/16 [00:00<?, ?it/s]

Loading files:   0%|          | 0/1 [00:00<?, ?it/s]

Saving to database: 0it [00:00, ?it/s]

Loading files:   0%|          | 0/1 [00:00<?, ?it/s]

...

Loading files:   0%|          | 0/1 [00:00<?, ?it/s]

Saving to database: 0it [00:00, ?it/s]

Loading files:   0%|          | 0/1 [00:00<?, ?it/s]

Saving to database: 0it [00:00, ?it/s]

<IPython.core.display.Javascript object>